# Fit di un segnale con gaussiane

# Spettro del colorante rosso


Importiamo le necessarie librerie

In [ ]:
import lmfit as lm
import lmfit.models as mod
import numpy as np
import matplotlib.pyplot as plt
%matplotlib inline
np.set_printoptions(threshold=50)


In [ ]:
%ls

In [ ]:
%%sh 
head rosso.txt

## Importazione dei dati
I dati sono molto spesso incolonnati in formato CSV, con una o più righe di intestazione informative che è necessario saltare.
Utilizzeremo la procedura di lettura generale genfromtxt di numpy.


In [ ]:
rosso = np.genfromtxt('rosso.txt', delimiter=',', skip_header=2, names=('nm','A'))
rosso

Abbiamo saltato due righe di intestazione e assegnato esplicitamente i nomi alle colonne.
Ora andiamo a visualizzare i nostri dati.

In [ ]:
nm=rosso['nm']
A=rosso['A']
plt.plot(nm,A)
plt.show()

Il nostro spettro si estende in zone dove non sarebbe opportuno analizzare i dati in termini di gaussiane. Perciò andremo a selezionare un intervallo di nm più adatto. 

In [ ]:
regione=(nm<570) & (nm> 430)
nm=nm[regione]
A=A[regione]
plt.plot(nm,A)
plt.show()

E' tempo di introdurre il nostro modello. Useremo la libreria di ottimizzazione lmfit che è dotata di molte utili funzionalità, fra queste dei comodi modelli preconfezionati e la possibilità di imporre vincoli sui parametri. Le alternative sono comunque numerose.

In [ ]:
g1=mod.GaussianModel(prefix='g1_')
pars=g1.make_params()
pars


Abbiamo suggerito un prefisso al modello GaussianModel, per avere nomi distinti sui parametri delle tre gaussiane. I modelli di lmfit possono essere combinati con le normali regole algebriche.

In [ ]:
modello=mod.GaussianModel(prefix='g1_') + mod.GaussianModel(
    prefix='g2_') + mod.GaussianModel(prefix='g3_')
pars=modello.make_params()
pars


In [ ]:
result=modello.fit(A,pars,x=nm)

result
print(result.fit_report())
plt.plot(nm, A,         'bo')
plt.plot(nm, result.init_fit, 'k--')
plt.plot(nm, result.best_fit, 'r-')
plt.show()

Non è avvenuta alcuna ottimizzazione, perchè i valori iniziali dei parametri non lo consentivano.
Bisogna impostarli a valori ragionevoli.

In [ ]:
mod1=mod.GaussianModel(prefix='g1_')
pars1=mod1.make_params(amplitude=10, center=530, sigma=5)
A1=mod1.eval(pars1, x=nm)
plt.plot(nm, A)
plt.plot(nm, A1)


Aggiustiamo i parametri finchè abbiamo una riproduzione approssimativa dello spettro.


In [ ]:
from ipywidgets import interact, interact_manual
import ipywidgets as wi
@interact_manual(
    a1=wi.FloatText(value=8.0), 
    s1=wi.FloatText(value=8.0),
    c1=wi.FloatText(value=525.0),
    a2=wi.FloatText(value=3.0), 
    s2=wi.FloatText(value=8.0),
    c2=wi.FloatText(value=490.0),
    a3=wi.FloatText(value=1.0), 
    s3=wi.FloatText(value=8.0),
    c3=wi.FloatText(value=460.0)
    )
def preliminare(a1, s1, c1, a2, s2, c2, a3, s3, c3):
    mod1=mod.GaussianModel(prefix='g1_')
    pars1=mod1.make_params(amplitude=a1, center=c1, sigma=s1)
    A1=mod1.eval(pars1, x=nm)
    mod2=mod.GaussianModel(prefix='g2_')
    pars2=mod2.make_params(amplitude=a2, center=c2, sigma=s2)
    A2=mod2.eval(pars2, x=nm)
    mod3=mod.GaussianModel(prefix='g3_')
    pars3=mod3.make_params(amplitude=a3, center=c3, sigma=s3)
    A3=mod3.eval(pars3, x=nm)
    plt.plot(nm, A, '.')
    plt.plot(nm, A1, label='g1')
    plt.plot(nm, A2, label='g2')
    plt.plot(nm, A3, label='g3')
    plt.plot(nm, A1 + A2 + A3, label='g1+g2+g3')
    plt.legend()
    plt.show()
    global pars
    pars=pars1+pars2+pars3


In [ ]:
result=modello.fit(A,pars,x=nm)

result
print(result.fit_report())
plt.plot(nm, A,         'bo')
plt.plot(nm, result.init_fit, 'k--', label='iniziale')
plt.plot(nm, result.best_fit, 'r-', label='best fit')
plt.legend()
plt.show()

Adesso fate lo stesso con i coloranti verde e blu.